In [1]:
import json
import os
import re
from collections import Counter,defaultdict
import pickle
import functools
import operator
import numpy as np
#simple tokenizer 529327
# from A1.dict_cons import SimpleTokenizer 
PATTERN = '''[ ,.:;"']+'''

In [2]:
class a():
    def __init__(self) -> None:
        self.a=22
        pass

    def fun1(self):
        print(1)
    def fun2(self):
        print(self.a)
    def fun3(self):
        self.b=55
        print(3)

class b(a):
    def __init__(self) -> None:
        b=3

        pass

    def fun1(self):
        print(4)
    def fun2(self):
        print(self.b)

obj = a()
obj.fun3()
obj.fun2()

3
22


In [2]:
from collections import Counter,defaultdict
import multiprocessing, re, json
import functools, operator
import operator
import pickle
from functools import partial
from matplotlib import pyplot as plt
import time
PATTERN = '''[ ,.:;"']+'''

class SimpleTokenizer():
    def __init__(self) -> None:
        
        pass

    def remove_non_ascii(self, text):
        return text.encode('ascii',errors='ignore').decode()
    
    def process_line(self, line):
        doc = json.loads(line.strip())

        text = doc['title'] +' ' + doc['abstract']
        text = text.encode('ascii',errors='ignore').decode()
        tokens = re.split(PATTERN, text)
        tokens = [token for token in tokens if token]

        return tokens
    
    def tokenize_parallel(self, path):
        with open(path,'r', encoding='utf-8') as file:
            lines = file.readlines()
            lines = set(lines)
            threads = max(multiprocessing.cpu_count()-2,1)
            pool = multiprocessing.Pool(threads) 
            result = pool.map(self.process_line, lines)
        
        result = functools.reduce(operator.iconcat, result, [])

        return set(result)
    
    def read_file(self, path):
        corpus =[]
        doc_ids = set()
        with open(path,'r', encoding='utf-8') as file:
            for doc in file:
                doc = json.loads(doc.strip())
                if doc['doc_id'] in doc_ids:
                    continue
                doc_ids.add(doc['doc_id'])
                text = doc['title'] +' ' + doc['abstract']
                corpus.append(self.remove_non_ascii(text))
        return corpus

    def seperate_words(self, corpus):
        all_tokens=[]
        for doc in corpus:
            tokens = re.split(PATTERN, doc)
            tokens = [token for token in tokens if token]
            all_tokens.extend(tokens)

        
        return all_tokens
    
    def save(self, data , path='./output.dict'):
        with open(path,'w') as file:
            file.write('\n'.join(data))

    def encode(self, path='./test'):
        corpus = self.read_file(path)
        # # print(corpus)
        tokens = self.seperate_words(corpus)

        # tokens = self.tokenize_parallel(path)
        self.save(list(set(tokens)), path='./output.dict')

    def encode_text(self,text):
        tokens = self.seperate_words([text])
        return tokens
    
class BPETokenizer(SimpleTokenizer):
    def __init__(self) -> None:
        self.merges = {}
        self.vocabulary = []
        self.splitted_word = {}
        self.word_freq = {}
        self.start_time = time.time()

    def read_file(self, path, portion=0.5):
        all_words =[]
        doc_ids =set()
        with open(path,'r', encoding='utf-8') as file:
            lines = file.readlines()
            lines = lines[int(len(lines)*portion):]

            for line in lines:
                doc = json.loads(line.strip())
                
                if doc['doc_id'] in doc_ids:
                    continue
                doc_ids.add(doc['doc_id'])
                text = doc['title'] +' ' + doc['abstract']
                all_words.extend(self.seperate_words(self.remove_non_ascii(text)))
                # corpus.append(self.remove_non_ascii(text))
        return all_words
    
    def seperate_words(self, doc):
        tokens = re.split(PATTERN, doc)
        tokens = [token+"Ġ" for token in tokens if token]
        return tokens
    
    def add_end_of_word(self, tokens):
        for i in range(len(tokens)):
            tokens[i] = tokens[i]+ "Ġ"
        return tokens
    
    def calc_freq(self, tokens):
        return Counter(tokens)
        # token_count = Counter()
        # for token in tokens:
        #     token_count[token]+=1
        
        # return token_count
    
    def split_words(self, words):
        splitted_word = {}
        vocabulary =set()

        for word in words:
            splitted_word[word] = list(word)
            vocabulary.update(splitted_word[word])

        vocabulary = list(vocabulary)
        vocabulary.sort()
        
        return splitted_word, vocabulary
       
    def split_words_query(self, words):
        splitted_word = []

        for word in words:
            splitted_word.append([ch for ch in word])

        return splitted_word

    def get_alphabets(self):
        # vocabulary = []
        # for word in self.word_freq.keys():
        #     for letter in word:
        #         if letter not in vocabulary:
        #             vocabulary.append(letter)

        vocabulary =set()
        for word in self.splitted_word.keys():
            vocabulary.update(self.splitted_word[word])

        vocabulary = list(vocabulary)
        vocabulary.sort()
        return vocabulary
    
    def calculate_pair_freq(self):
        pair_count = Counter()
        
        # c = Counter(zip(seq, seq[1:]))
        for word in self.word_freq.keys():
        # for word, charaters in self.splitted_word.items():
            charaters = self.splitted_word[word]
            # pair_count.update(zip(charaters, charaters[1:])*self.word_freq[word])
            n = len(charaters)

            for i in range(n -1):
                pair_count[(charaters[i], charaters[i+1])] += self.word_freq[word]
            
        return pair_count
    
    def parallel_pair_freq(self, data):
        pair_count = Counter()
        # charaters, freq = data
        for charaters, freq in data:
            n = len(charaters)

            for i in range(n -1):
                pair_count[(charaters[i], charaters[i+1])] += freq
                
            return pair_count
    
    def chunk(self, arr_range, arr_size):
        arr_range = iter(arr_range)
        return iter(lambda: tuple(islice(arr_range, arr_size)), ())

    def calculate_pair_freq_parallel(self):
        pair_count = Counter()
        
        # c = Counter(zip(seq, seq[1:]))

        threads = max(multiprocessing.cpu_count()-2,1)
        pool = multiprocessing.Pool(threads) 
        # tokens = list(self.word_freq.keys())
        # tokens = np.array_split(tokens, threads)
        inp = list(zip(self.splitted_word.values(), self.word_freq.values() ))
        # inp = np.array_split(inp, threads)
        inp =list(self.chunk(inp, threads))
        # N = pool.map(partial(self.parallel_pair_freq, b=second_arg), a_args)

        pair_count.update(dict(pool.map(self.parallel_pair_freq, inp)))
            
        return pair_count

    def get_best_pair(self, pair_freq):
        v = list(pair_freq.values())
        k = list(pair_freq.keys())
        return k[v.index(max(v))]
        max_val = max(pair_freq.values())
        ret = list(filter(lambda x: pair_freq[x] == max_val, pair_freq))[0]
        return ret, max_val
    
    def merges_best_pair(self, best_pair):

        for word in self.splitted_word.keys():
            # n=len(split)
            split = self.splitted_word[word]
            if len(split)==1:
                continue
            
            i=0
            while i< len(split) - 1:
                if split[i] == best_pair[0] and split[i+1] == best_pair[1]:
                    # split = split[:i] + [best_pair[0]+best_pair[1]] + split[i+2:]
                    split[i] =best_pair[0]+best_pair[1]
                    split.pop(i+1)
                
                i+=1
            
            # self.splitted_word[word] = split
        
        return 1
    
    def first_itr(self, path):
        # corpus = self.read_file(path)
        # words = self.seperate_words(corpus)
        # words = self.add_end_of_word(words)
        words = self.read_file(path)

        self.word_freq = self.calc_freq(words)
        self.splitted_word, self.vocabulary = self.split_words(self.word_freq.keys())
        # self.vocabulary = self.get_alphabets()
        
    def train(self, merges=100):
        points = [time.time()-self.stat_time]
        for i in range(merges):
            pair_frequencies = self.calculate_pair_freq()
            if len(pair_frequencies) ==0:
                break
            # best_pair, count = self.get_best_pair(pair_frequencies)
            best_pair = self.get_best_pair(pair_frequencies)
            self.merges[best_pair] = best_pair[0]+best_pair[1]
            self.vocabulary.append(self.merges[best_pair])
            self.merges_best_pair(best_pair)
            # print(best_pair,i)
            points.append(time.time()-self.stat_time)
        
        self.save(self.vocabulary, './output.dict')
        # del self.splitted_word
        # del self.word_freq
        # del self.vocabulary
        plt.plot(points)
        plt.xlabel('#Merges')
        plt.ylabel('Time(sec)')
        plt.title('BPE')
        plt.savefig('./BPE_progress.png')
        return
    
    def encode_text(self, text):
        words = self.seperate_words(text)
        words = self.add_end_of_word(words)
        splitted_words = self.split_words_query(list(set(words)))
        n=len(splitted_words)
        for pair in self.merges.keys():
            for i in range(n):
                split= splitted_words[i]
                j=0
                while j < len(split)-1:
                    if split[j] == pair[0] and split[j+1] == pair[1]:
                        split = split[:j] + [self.merges[pair]] + split[j+2:]
                    j+=1
                splitted_words[i]=split
        
        tokens =  sum(splitted_words, [])
        return tokens

# Question 1
# obj =SimpleTokenizer()
# bpe =BPETokenizer()
# bpe.first_itr('test')

# obj.encode('cord19-trec_covid-docs')

In [26]:
bpe.first_itr('cord19-trec_covid-docs')

In [4]:
bpe.get_best_pair(bpe.pa)

In [13]:
# MultiProcessng
import multiprocessing
from multiprocessing import Process, Semaphore, Lock,Pool

# import time
# pool = multiprocessing.Semaphore(max(multiprocessing.cpu_count()-2,1)) 
# pool = multiprocessing.Pool() 
# pool = multiprocessing.Pool(processes=4) 
# outputs = pool.map(square, inputs) 
# 
def remove_non_ascii( text):
    return text.encode('ascii',errors='ignore').decode()

def process_line(line):
    doc = json.loads(line.strip())

    text = doc['title'] +' ' + doc['abstract']
    text = text.encode('ascii',errors='ignore').decode()
    tokens = re.split(PATTERN, text)
    tokens = [token for token in tokens if token]

    return tokens

def read_file( path):
    all_words = []
    doc_ids = set()
    with open(path,'r', encoding='utf-8') as file:
        lines = file.readlines()
        # with Pool(4) as p:  # Create a pool with 4 worker processes
        #     result = p.map(process_line, lines)

        threads = max(multiprocessing.cpu_count()-2,1)
        pool = multiprocessing.Pool(threads) 
        result = pool.map(process_line, lines)

    return result

def seperate_words( doc):
    tokens = re.split(PATTERN, doc)
    tokens = [token for token in tokens if token]
    return tokens

ret = read_file('cord19-trec_covid-docs')

In [1]:
# import multiprocessing

# def double(a):
#     return a * 2

# def driver_func():
#     PROCESSES = 4
#     with multiprocessing.Pool(PROCESSES) as pool:
#         params = [(1, ), (2, ), (3, ), (4, )]
#         results = [pool.apply_async(double, p) for p in params]

#         for r in results:
#             print('\t', r.get())
# driver_func()

In [12]:
class WordPieceTokenizer(SimpleTokenizer):
    def __init__(self) -> None:
        self.merges = {}
        self.vocabulary = set()
        self.splitted_words = {}
        self.word_freq = {}
        # words = self.get_all_words(path,full)

        # self.word_freq = self.calc_freq(words)
        # self.splitted_words = self.split_words(words)
        # self.vocabulary = ['[PAD]', '[UNK]', '[CLS]', '[SEP]', '[MASK]']
        # self.merges={}
        # del words
        # self.training()

    def read_file(self, path, portion=0.5):
        all_words =[]
        doc_ids =set()
        with open(path,'r', encoding='utf-8') as file:
            lines = file.readlines()
            

            lines = lines[int(len(lines)*portion):]

            for line in lines:
                doc = json.loads(line.strip())
                
                if doc['doc_id'] in doc_ids:
                    continue
                doc_ids.add(doc['doc_id'])
                text = doc['title'] +' ' + doc['abstract']
                all_words.extend(self.seperate_words(self.remove_non_ascii(text)))
                # corpus.append(self.remove_non_ascii(text))
        return all_words
    
    def calc_freq(self, tokens):
        return Counter(tokens)
    
    def seperate_words(self, doc):
        tokens = re.split(PATTERN, doc)
        tokens = [token for token in tokens if token]
        return tokens
    
    def split_words(self, tokens):
        splitted_word = {}
        vocabulary = set()
        for word in tokens:
            splitted_word[word] = ["$$"+ch for ch in word]
            splitted_word[word][0] = splitted_word[word][0][2:]
            vocabulary.union(splitted_word[word])

        return splitted_word, vocabulary
    
    def get_vocabulary(self):
        vocabulary = []

        # for word in self.word_freq.keys():
        #     for letter in word:
        #         if letter not in vocabulary:
        #             vocabulary.append(letter)
        vocabulary =set()
        for word in self.splitted_words.keys():
            vocabulary.union(self.splitted_words[word])

        vocabulary = list(vocabulary)
        vocabulary.sort()
        return vocabulary
    
    def get_best_pair(self, pair_freq):
        v = list(pair_freq.values())
        k = list(pair_freq.keys())
        return k[v.index(max(v))]
    
    #score(A,B) = (freq(AB)*len(vocab))/ (freq(A)*freq(B))
    def calculate_pair_score(self):
        letter_count = Counter()
        pair_count = Counter()

        for word in self.word_freq.keys():
            charaters = self.splitted_words[word]
            n=len(charaters)
            freq = self.word_freq[word]
            if n==1:
                letter_count[charaters[0]]+=freq
                continue

            for i in range(n-1):
                pair = (charaters[i], charaters[i+1])
                pair_count[pair] += freq
                letter_count[charaters[i]] +=freq

            letter_count[charaters[-1]] += freq

        score ={}
        for pair in pair_count.keys():
            score[pair] = pair_count[pair] /(letter_count[pair[0]] * letter_count[pair[1]])
        
        return score

    def merges_best_pair(self, best_pair):

        for word in self.splitted_words.keys():
            split = self.splitted_words[word]
            # n=len(split)
            if len(split)==1:
                continue
            
            i=0
            while i< len(split) - 1:
                if split[i] == best_pair[0] and split[i+1] == best_pair[1]:
                    merge = best_pair[0] + best_pair[1][2:]
                    split = split[:i] + [merge] + split[i+2:]
                
                i+=1
            
            self.splitted_words[word] = split
            # print(split)
        
        return 1
        
    def first_itr(self, path):
        # corpus = self.read_file(path)
        # words = self.seperate_words(corpus)
        # words = self.add_end_of_word(words)
        words = self.read_file(path)

        self.word_freq = self.calc_freq(words)
        self.splitted_words, self.vocabulary = self.split_words(self.word_freq.keys())
        # self.vocabulary = self.get_alphabets()

    def train(self, k=500):

        for i in range(k):
            # print(self.vocabulary)
            score = self.calculate_pair_score()
            if len(score) ==0:
                break
            best_pair = self.get_best_pair(score)

            self.merges[best_pair] = best_pair[0] + best_pair[1][2:]
            self.merges_best_pair(best_pair)
            print(self.merges[best_pair])
            self.vocabulary.add(self.merges[best_pair])
            # print(merges)
            # print(i)
        return
    
    def encode_word(self, word):
        tokens = []
        while len(word)>0:
            i=len(word)

            while i>0 and word[:i] not in self.vocabulary:
                i-=1
            
            if i==0:
                return ["[UNK]"]
            
            tokens.append(word[:i])
            word = word[i:]

            if len(word) >0:
                word = '$$'+word

        return tokens
    
    def encode(self, path='test', portion =0.5):
        all_words = self.read_file(path, portion)
        tokens = []
        for word in all_words:
            tokens.extend(self.encode_word(word))
        
        return all_words

    def encode_text(self, text):
        words = self.seperate_words(text)

        tokens = []
        for word in words:
            tokens.extend(self.encode_word(word))
        
        return tokens

wpe = WordPieceTokenizer()
wpe.first_itr('test')


In [11]:
wpe.get_best_pair(wpe.calculate_pair_score())

('$$$', '$$#')

In [13]:
wpe.train(20)

$$$#
0
$$**
1
Q_
2
Q_3
3
Q_37
4
$$#8
5
$$4#8
6
$$(+
7
$$W!
8
$$OW!
9
NOW!
10
//
11
~7
12
$$7#
13
$$T#
14
$$T#2
15
#2
16
~78
17
$$/~
18
$$~2
19


In [12]:
# from A1.dict_cons import SimpleTokenizer, BPETokenizer, WordPieceTokenizer
# from collections import Counter,defaultdict
# import json
import pickle
import numpy as np

class InvertedIndex():
    def __init__(self) -> None:
        # if tokenizer==0:
        #     self.encoder = SimpleTokenizer()
        # elif tokenizer==1:
        #     self.encoder = BPETokenizer()
        # elif tokenizer==2:
        #     self.encoder = WordPieceTokenizer()
        # self.encoder = tokenizer
        self.inverted_index = defaultdict(lambda: [])
        self.doc_to_index={}
        self.index_to_doc={}
        self.number_docs = 0
        self.IDF = {}

        # self.doc_count = Counter()
    
    def numerize_docid(self,doc_count):
        # self.doc_to_index = {item[0]:idx for idx, item in enumerate(sorted(doc_count.items(), key=lambda item: item[1],reverse=True))}
        for idx, item in enumerate(sorted(doc_count.items(), key=lambda item: item[1],reverse=True)):
            self.doc_to_index[item[0]] = idx
            self.index_to_doc[idx] = item[0]
        
        self.number_docs = len(self.doc_to_index)

    def get_idf(self,df):
        return np.log2(1 + self.number_docs/df)
    
    def get_TF(self,tf):
        if tf ==0:
            return 0
        return 1+ np.log2(tf)
        
    def populate_variables(self):
        self.normalization_value =np.zeros(self.number_docs)

        for token in self.inverted_index.keys():
            doc_list = self.inverted_index[token]
            IDF = self.get_idf(len(doc_list))
            self.IDF[token] = IDF
            posting_dict = {}
            for doc_id, token_freq in doc_list:
                doc_index = self.doc_to_index[doc_id]
                tf = self.get_TF(token_freq)
                self.normalization_value[doc_index] += np.square(tf*IDF)
                posting_dict[doc_index] = tf

            self.inverted_index[token] = posting_dict
        
        self.normalization_value = np.sqrt(self.normalization_value)

    def construct_index(self, encoder, path='test'):
        doc_count = Counter()
        i=0
        doc_ids = set()
        with open(path,'r', encoding='utf-8') as file:
            for doc in file:
                print(i)
                i+=1
                doc = json.loads(doc.strip())
                if doc['doc_id'] in doc_ids:
                    continue
                doc_ids.add(doc['doc_id'])
                text = doc['title'] +' ' + doc['abstract']
                text = encoder.remove_non_ascii(text)
                tokens = encoder.encode_text(text)
                token_freq = Counter(tokens)
                tokens = set(tokens)
                doc_count[doc['doc_id']]+=len(token_freq.keys())
                for token in tokens:
                    self.inverted_index[token].append((doc['doc_id'],token_freq[token]))
        
        self.numerize_docid(doc_count)
        self.populate_variables()
        
        encoder.save(self.inverted_index.keys(), './indexfile.dict')
        data = {
                'doc_to_index': self.doc_to_index, 
                'inverted_index': dict(self.inverted_index),
                'index_to_doc': self.index_to_doc,
                'number_docs': self.number_docs,
                'IDF': self.IDF,
                'normalization_value': self.normalization_value
             }
        if type(encoder)!=SimpleTokenizer:
            data['merges'] = encoder.merges
            data['vocabulary'] = encoder.vocabulary
        self.save_binary(data)
         
    def save_binary(self, data, path='indexfile.idx'):
        with open(path, 'wb') as f:
            pickle.dump(data, f)
    
    def read_binary(self, path='indexfile.idx'):
        with open(path, 'rb') as f:
            loaded_dict = pickle.load(f)
        return loaded_dict


In [7]:
obj = InvertedIndex()
encoder = SimpleTokenizer()
# obj.construct_index(path='cord19-trec_covid-docs', encoder=bpe)
# obj.construct_index(path='test', encoder=bpe)

In [29]:
a=[(1,2),(3,4)]
a

(3, 4)

In [7]:
class Retrival():
    def __init__(self, encoder, index_file_path='./indexfile.idx') -> None:
        self.encoder = encoder
        # # self.IDF = {}
        self.inverted_index = {}
        self.doc_to_index={}
        self.index_to_doc={}
        self.number_doc = 0
        self.normalization_term = []
        self.load_parameters(index_file_path)
        return
    
    def read_indexfile(self, path= './indexfile.idx'):
        with open(path, 'rb') as f:
            loaded_dict = pickle.load(f)
        return loaded_dict
    
    def load_parameters(self, path='./indexfile.idx'):
        ret = self.read_indexfile(path)
        self.inverted_index = ret['inverted_index']
        self.doc_to_index = ret['doc_to_index']
        self.IDF = ret['IDF']
        self.index_to_doc=ret['index_to_doc']
        self.number_doc = ret['number_docs']
        self.normalization_term = ret['normalization_value']
        if type(self.encoder)!=SimpleTokenizer:
            self.encoder.merges = ret['merges']
            self.encoder.vocabulary = ret['vocabulary']

    def process_doc(self, doc):
        text = doc['title'] +' ' + doc['abstract']
        text = self.encoder.remove_non_ascii(text)
        return self.encoder.encode_text(text)
    
    def process_query(self, doc):
        # doc = json.loads(doc.strip())
        text = doc['title'] +' ' + doc['description'] +' ' + doc['narrative']
        text = self.encoder.remove_non_ascii(text)
        tokens = self.encoder.encode_text(text)
        
        token_count = Counter()
        for token in tokens:
            token_count[token]+=1
            
        return set(tokens), token_count
    
    def get_TF(self,tf):
        if tf ==0:
            return 0
        return 1+ np.log2(tf)
    
    def log_normalized_tf(self, tf):
        # for i in range(len(tf)):
        #     if tf[i]!=0:
        #         tf[i] = 1+ np.log2(tf[i])

        # zero_mask = (tf == 0)
        # tf = 1+ np.where(zero_mask, 0, np.log(tf))
        
        # tf = np.where(tf > 0, 1+np.log(tf), 1)

        # tf[tf!=0] = 1+ np.log2(tf[tf!=0])
        # tf[tf==0]=1
        tf[tf!=0] = np.log2(tf[tf!=0])
        tf = 1+ tf
        return tf
    
    def train_tf_idf(self, path = './test'):
        inverted_index = defaultdict(lambda: set())
        doc_count = Counter()
        with open(path,'r', encoding='utf-8') as file:
            collection= file.readlines()
            self.number_doc =len(collection)
            tf = defaultdict(lambda: np.zeros(self.number_doc))
            # tf = np.zeros()
            doc_index= 0
            for doc in collection:
                doc = json.loads(doc.strip())
                tokens = self.process_doc(doc)
                
                no_tokens = len(set(tokens))
                doc_count[doc['doc_id']]+=no_tokens
                for token in tokens:
                    # inverted_index[token].append(doc['doc_id'])
                    # tf[token][doc_index]+=1
                    tf[token][doc_index]+=1
                    inverted_index[token].add(doc['doc_id'])

                    
                
                self.doc_to_index[doc['doc_id']] = doc_index
                self.index_to_doc[doc_index] = doc['doc_id']
                doc_index+=1
                # print(doc_index)
        print('-----Documents processed-----')
        IDF = {token:np.log2(self.number_doc/len(set(docs))) for token, docs in inverted_index.items()}
        print('-----IDF calculated-----')
        self.tf_idf = {token : self.log_normalized_tf(tf[token])*IDF[token] for token in tf.keys()}
        print('-----TF-IDF calculated-----')
        normalization_term = np.zeros(self.number_doc)
        for token in self.tf_idf.keys():
            normalization_term += np.square(self.tf_idf[token])
        self.normalization_term = np.sqrt(normalization_term)
        print('-----Normalization Term calculated-----')

    def tf_idf_query(self, token_freq):
        query_tf_idf = {}
        normalization_term = 0.0
        for token, freq in token_freq.items():
            query_tf_idf[token] = (1+ np.log2(freq))*self.IDF[token]
            normalization_term+=np.square(query_tf_idf[token])
        
        return query_tf_idf, np.sqrt(normalization_term)
    
    def calculate_similarities(self, query):
        tokens, token_freq = self.process_query(query)
        query_tf_idf, query_normalization_term = self.tf_idf_query(token_freq)
        
        similarity = []
        all_tokens = set(self.tf_idf.keys())
        tokens = all_tokens.intersection(tokens)
        for doc_index in range(self.number_doc):
            sim = 0.0
            
            for token in tokens:
                # print(token, doc_index)
                sim += query_tf_idf[token] * self.tf_idf[token][doc_index]
            sim = sim/(query_normalization_term * self.normalization_term[doc_index])
            print(doc_index, sim)
            similarity.append((self.index_to_doc[doc_index], sim))
            
        similarity = sorted(similarity, key=lambda item: item[1], reverse=True)
        return similarity
    
    def run_query(self, query):
        tokens, token_freq = self.process_query(query)
        query_tf_idf, query_normalization_term = self.tf_idf_query(token_freq)
        
        similarity = []
        # all_tokens = set(self.tf_idf.keys())
        # tokens = all_tokens.intersection(tokens)

        for doc_index in range(self.number_doc):
            sim = 0.0
            
            for token in tokens:
                # print(token, doc_index)
                if doc_index in self.inverted_index[token].keys():
                    sim += query_tf_idf[token] * self.inverted_index[token][doc_index]
            sim = sim/(query_normalization_term * self.normalization_term[doc_index])
            print(doc_index, sim)
            similarity.append([query['query_id'], 0, self.index_to_doc[doc_index], sim])
            
        similarity = sorted(similarity, key=lambda item: item[1], reverse=True)
        return similarity[:100]
    
    def save(self, data , path):
        with open(path,'w') as file:
            for line in data:
                file.write('\t'.join(line))
                file.write('\n')

    def retrieve(self, path = './cord19-trec_covid-queries', output_path = './resultfile'):
        ret = [['qid', 'iteration', 'docid', 'relevancy']]
        n=0
        # start
        with open(path,'r', encoding='utf-8') as file:
            for query in file:
                doc = json.loads(query.strip())
                result = self.run_query(doc)

        self.save(data=result, path=output_path)
        return result
    
    def read_qrel(self, path = 'cord19-trec_covid-qrels'):
        self.result_gt = defaultdict(set)
        with open(path,'r', encoding='utf-8') as file:
            for rel in file:
                doc = json.loads(rel.strip())
                if doc['relevance']==0:
                    self.result_gt[doc['query_id']]['irrelevent'].add(self.doc_to_index(doc['doc_id']))
                else:
                    self.result_gt[doc['query_id']]['relevent'].add(self.doc_to_index(doc['doc_id']))

    def parse_result(self,result):
        ret = defaultdict(set)

        for entry in result:
            ret[entry[0]].add(entry[2])

        return ret
    
# F = 2RP/(R+P)
    def score(self, relevent, irrelevent, retrieved, k=10):
        relevent = set(list(relevent)[:k])
        irrelevent = set(list(irrelevent)[:k])
        retrieved = set(list(retrieved)[:k])
        relevent_and_retrieved = len(retrieved.intersection(relevent))
        precision = relevent_and_retrieved/len(retrieved)
        recall = relevent_and_retrieved/len(relevent)
        F = 2*recall*precision/(recall+precision)
        return F

    def calculate_score(self, result):
        scores={10:0, 20:0, 50:0, 100:0}
        for query_id in result.keys():
            relevent = self.result_gt[query_id]['relevent']
            irrelevent = self.result_gt[query_id]['irrrelevent']
            retrieved = result[query_id]
            scores[10] += self.score(relevent, irrelevent, retrieved, 10)
            scores[20] += self.score(relevent, irrelevent, retrieved, 20)
            scores[50] += self.score(relevent, irrelevent, retrieved, 50)
            scores[100] += self.score(relevent, irrelevent, retrieved, 100)
        n=len(result.keys())

        score = {k:v/n for k,v in score.items()}

        return score






In [31]:
        scores={10:0, 20:0, 50:0, 100:0}
scores

{10: 0, 20: 0, 50: 0, 100: 0}

In [21]:
a = defaultdict(dict)
a['a']['b']=10
a

defaultdict(dict, {'a': {'b': 10}})

In [19]:
data=[]
with open('output.dict','r', encoding='utf-8') as file:
    for line in file:
        data.append(line.strip())

In [8]:
retr = Retrival(encoder=bpe)

In [9]:
with open('./cord19-trec_covid-queries','r', encoding='utf-8') as file:
    for query in file:
        doc = json.loads(query.strip())
        print(retr.process_query(doc))
        

({'wh', 'missionĠ', 'k', 'theĠ', 'C', 'ingĠ', 'anim', 'andĠ', 'isĠ', 'hum', 'a', 'ev', 'ab', '-', 'intoĠ', 'ang', 'ansĠ', 'e', 'includingĠ', 'firstĠ', 'AR', 'ol', 'r', 'sĠ', 'V', '2Ġ', 'on', 'itsĠ', 'ur', 'ationĠ', 'orm', '9Ġ', 'inf', 'ig', 'alĠ', 'trans', 'c', 'virusĠ', 'I', 'cor', 'outĠ', 'se', 'S', '1', 'utionĠ', 'inĠ', 'or', 'ofĠ', 'eĠ', 'atĠ', 'o', 'O', 'D', 'Ġ', 'V-', 's'}, Counter({'Ġ': 24, 'C': 2, '-': 2, 'virusĠ': 2, 'S': 2, 'o': 2, 'eĠ': 2, 'ab': 1, 'outĠ': 1, 'O': 1, 'V': 1, 'I': 1, 'D': 1, '1': 1, '9Ġ': 1, 'theĠ': 1, 'trans': 1, 'missionĠ': 1, 'firstĠ': 1, 'itsĠ': 1, 'hum': 1, 'ansĠ': 1, 'cor': 1, 'on': 1, 'a': 1, 'ev': 1, 'ol': 1, 'utionĠ': 1, 'intoĠ': 1, 'anim': 1, 'alĠ': 1, 'wh': 1, 'atĠ': 1, 'ofĠ': 1, 'inf': 1, 'orm': 1, 'ationĠ': 1, 'andĠ': 1, 'AR': 1, 'V-': 1, '2Ġ': 1, 'r': 1, 'ang': 1, 's': 1, 'ur': 1, 'c': 1, 'or': 1, 'ig': 1, 'inĠ': 1, 'se': 1, 'e': 1, 'k': 1, 'ingĠ': 1, 'includingĠ': 1, 'sĠ': 1, 'isĠ': 1}))
({'do', 'missionĠ', 'k', 'condi', 'theĠ', 'h', 'C', 'ingĠ

In [36]:
retr.retrieve()

0 0.4893629939461597
1 0.5729971656886792
2 0.5723184255800465
3 0.5109521030361971
4 0.5410673656753132
5 0.5405982780629628
6 0.5574986895736169
7 0.5828624524356351
8 0.5665448464787449
9 0.5615490219967073
10 0.5729828085913252
11 0.5357481386813567
12 0.5936795267374881
13 0.5964295053565569
14 0.5895484503292663
15 0.5441194743682141
16 0.5632500817130592
17 0.5343445491435498
18 0.5491899584201313
19 0.591002523709054
20 0.5791660112843697
21 0.5695667655826795
22 0.5749726371874105
23 0.5248381938043393
24 0.612106182719475
25 0.6037453230178954
26 0.5955951451862997
27 0.5540975861794498
28 0.6097080625325011
29 0.5880606226418936
30 0.5277407591436805
31 0.5996485832077053
32 0.6019620584686227
33 0.5738012596308507
34 0.5810474623744518
35 0.5866011092253742
36 0.550142696655722
37 0.5978555975882435
38 0.6291339921058763
39 0.5663405338282382
40 0.5895320746481988
41 0.6047767910337276
42 0.5076960076586757
43 0.6212352083373762
44 0.6366926483905473
45 0.5731716633242574
4

[[('4hcs0z65', 0.7741625312216172),
  ('6fti2z37', 0.7595334874849505),
  ('huo2czjf', 0.7567570310271057),
  ('fu8on8kx', 0.7566503901732118),
  ('33fs6exl', 0.7520537664333569),
  ('4tiyjc0p', 0.7502748053804151),
  ('hygxwl2f', 0.7483692124544407),
  ('beo6ol29', 0.7483436271299835),
  ('nfc018kr', 0.74783734587249),
  ('jzv7dp50', 0.746853223771236),
  ('knbf8m4x', 0.7459935525936668),
  ('8qfgke03', 0.7458173982703493),
  ('g3a9onb5', 0.7457109402459937),
  ('7xuxesi3', 0.7453964238001062),
  ('9m6xwi6f', 0.7453107358680364),
  ('q9rn75qb', 0.7451021743736951),
  ('gpnk6t59', 0.7433717531741867),
  ('4psg0z3n', 0.7433570003173533),
  ('rnskg79a', 0.7417373288973221),
  ('sp6gm42a', 0.7405425802740367),
  ('77k2nz8h', 0.740507248040632),
  ('5r9i4y8m', 0.7404204669556989),
  ('dm6pq1sa', 0.740362420288591),
  ('4r2jlc7k', 0.7403423318164482),
  ('xjk1h2rx', 0.739911627392587),
  ('975vahqf', 0.7388417356397572),
  ('toukgabx', 0.7387765674410858),
  ('d752zg2b', 0.7387306717335717)

In [133]:
len(obj.index_to_doc)

191175

In [117]:
a=Counter(['a','b','a'])
a = dict(a)
a = Counter(a)

In [119]:
a =[('a',10),('b',20)]
Counter(a)

Counter({('a', 10): 1, ('b', 20): 1})

In [8]:
def read_indexfile( path):
    with open(path, 'rb') as f:
        loaded_dict = pickle.load(f)
    return loaded_dict

In [11]:
ret = read_indexfile('./indexfile.idx')

In [15]:
ret.keys()

dict_keys(['doc_to_index', 'inverted_index'])

In [ ]:
import numpy as np
from collections import Counter, defaultdict
import json
import pickle

class Retrival():
    def __init__(self, encoder) -> None:
        self.encoder = encoder
        self.IDF = {}
        self.tf_idf = {}
        self.doc_to_index={}
        self.index_to_doc={}
        self.number_doc = 0
        self.normalization_term = []

        return

    def read_indexfile(self, path= './indexfile.idx'):
        with open(path, 'rb') as f:
            loaded_dict = pickle.load(f)
        return loaded_dict
    
    def load_inverted_index(self, path='./indexfile.idx'):
        ret = self.read_indexfile(path)
        inverted_index = ret['inverted_index']
        self.doc_to_index = ret['doc_to_index']

    def process_doc(self, doc):
        text = doc['title'] +' ' + doc['abstract']
        text = self.encoder.remove_non_ascii(text)
        return self.encoder.encode_text(text)
    
    def process_query(self, doc):
        # doc = json.loads(doc.strip())
        text = doc['title'] +' ' + doc['description'] +' ' + doc['narrative']
        text = self.encoder.remove_non_ascii(text)
        tokens = self.encoder.encode_text(text)
        
        token_count = Counter()
        for token in tokens:
            token_count[token]+=1
            
        return set(tokens), token_count
    
    def log_normalized_tf(self, tf):
        # for i in range(len(tf)):
        #     if tf[i]!=0:
        #         tf[i] = 1+ np.log2(tf[i])

        # zero_mask = (tf == 0)
        # tf = 1+ np.where(zero_mask, 0, np.log(tf))
        
        # tf = np.where(tf > 0, 1+np.log(tf), 1)

        # tf[tf!=0] = 1+ np.log2(tf[tf!=0])
        # tf[tf==0]=1
        tf[tf!=0] = np.log2(tf[tf!=0])
        tf = 1+ tf
        return tf
    
    def double_normalized_tf(tf):
        max_freq = max(tf)
        tf = 0.5 + 0.5*tf/max_freq
        # for j in range(len(tf)):
        #     if tf[j]!=0:
        #         tf[j] = 0.5 + 0.5 * tf[j]/max_freq
        
        return tf
    
    def train_tf_idf(self, path = './test'):
        inverted_index = defaultdict(lambda: set())
        doc_count = Counter()
        with open(path,'r', encoding='utf-8') as file:
            collection= file.readlines()
            self.number_doc =len(collection)
            tf = defaultdict(lambda: np.zeros(self.number_doc))
            # tf = np.zeros()
            doc_index= 0
            for doc in collection:
                doc = json.loads(doc.strip())
                tokens = self.process_doc(doc)
                
                no_tokens = len(set(tokens))
                doc_count[doc['doc_id']]+=no_tokens
                for token in tokens:
                    # inverted_index[token].append(doc['doc_id'])
                    # tf[token][doc_index]+=1
                    tf[token][doc_index]+=1
                    inverted_index[token].add(doc['doc_id'])

                    
                
                self.doc_to_index[doc['doc_id']] = doc_index
                self.index_to_doc[doc_index] = doc['doc_id']
                doc_index+=1
                # print(doc_index)
        print('-----Documents processed-----')
        IDF = {token:np.log2(self.number_doc/len(set(docs))) for token, docs in inverted_index.items()}
        print('-----IDF calculated-----')
        self.tf_idf = {token : self.log_normalized_tf(tf[token])*IDF[token] for token in tf.keys()}
        print('-----TF-IDF calculated-----')
        normalization_term = np.zeros(self.number_doc)
        for token in self.tf_idf.keys():
            normalization_term += np.square(self.tf_idf[token])
        self.normalization_term = np.sqrt(normalization_term)
        print('-----Normalization Term calculated-----')

    def tf_idf_query(self, token_freq):
        query_tf_idf = {}
        normalization_term = 0.0
        for token, freq in token_freq.items():
            query_tf_idf[token] = (1+ np.log2(freq))*self.IDF[token]
            normalization_term+=np.square(query_tf_idf[token])
        
        return query_tf_idf, np.sqrt(normalization_term)
    
    def calculate_similarities(self, query):
        tokens, token_freq = self.process_query(query)
        query_tf_idf, query_normalization_term = self.tf_idf_query(token_freq)
        
        similarity = []
        all_tokens = set(self.tf_idf.keys())
        tokens = all_tokens.intersection(tokens)
        for doc_index in range(self.number_doc):
            sim = 0.0
            
            for token in tokens:
                # print(token, doc_index)
                sim += query_tf_idf[token] * self.tf_idf[token][doc_index]
            sim = sim/(query_normalization_term * self.normalization_term[doc_index])
            print(doc_index, sim)
            similarity.append((self.index_to_doc[doc_index], sim))
            
        similarity = sorted(similarity, key=lambda item: item[1], reverse=True)
        return similarity
    def retrieve(self, path = './cord19-trec_covid-queries'):
        result = [[]]
        with open(path,'r', encoding='utf-8') as file:
            for query in file:
                doc = json.loads(doc.strip())



In [71]:
encoder = SimpleTokenizer()
inverted_index = defaultdict(lambda: set())
document_freq = Counter()
doc_count = Counter()
doc_to_index = {}
token_to_index ={}
number_doc = 0
# encoder

with open('test','r', encoding='utf-8') as file:
    collection= file.readlines()
    number_doc =len(collection)
    tf = defaultdict(lambda: np.zeros(number_doc))
    # tf = np.zeros()
    doc_index= 0
    for doc in collection:
        doc = json.loads(doc.strip())
        tokens = process_doc(encoder, doc)
        
        no_tokens = len(set(tokens))
        doc_count[doc['doc_id']]+=no_tokens
        for token in tokens:
            # inverted_index[token].append(doc['doc_id'])
            # tf[token][doc_index]+=1
            tf[token][doc_index]+=1
            inverted_index[token].add(doc['doc_id'])

            
        
        doc_to_index[doc['doc_id']] = doc_index
        doc_index+=1
        # print(doc_index)

print('-----Documents processed-----')
IDF = {token:np.log2(number_doc/len(set(docs))) for token, docs in inverted_index.items()}
print('-----IDF calculated-----')
tf_idf = {token : log_normalized_tf(tf[token])*IDF[token] for token in tf.keys()}
print('-----TF-IDF calculated-----')

normalization_term = np.zeros(number_doc)
for token in tf_idf.keys():
    normalization_term += np.square(tf_idf[token])
normalization_term = np.sqrt(normalization_term)
print('-----Normalization Term calculated-----')

-----Documents processed-----


In [81]:
def process_query(doc, encoder):
    doc = json.loads(doc.strip())
    text = doc['title'] +' ' + doc['description'] +' ' + doc['narrative']
    text = encoder.remove_non_ascii(text)
    tokens = encoder.encode_text(text)
    
    token_count = Counter()
    for token in tokens:
        token_count[token]+=1
        
    return set(tokens), token_count

def tf_idf_query(token_freq, idf):
    tf_idf = {}
    normalization_term = 0.0
    for token, freq in token_freq.items():
        tf_idf[token] = (1+ np.log2(freq))*idf[token]
        normalization_term+=np.square(tf_idf[token])
    
    return tf_idf, np.sqrt(normalization_term)


In [ ]:
with open('cord19-trec_covid-queries','r', encoding='utf-8') as file:
    for line in file:
        tokens, token_freq = process_query(line, encoder)
        query_tf_idf, query_normalization_term = tf_idf_query(token_freq, IDF)
        
        similarity = []
        all_tokens = set(tf_idf.keys())
        tokens = all_tokens.intersection(tokens)
        for doc_index in range(number_doc):
            sim = 0.0
            
            for token in tokens:
                # print(token, doc_index)
                sim += query_tf_idf[token] * tf_idf[token][doc_index]
            sim = sim/(query_normalization_term * normalization_term[doc_index])
            print(doc_index, sim)
            similarity.append((doc_index, sim))



        break


In [ ]:
max(similarity)
sorted_by_second = sorted(similarity, key=lambda tup: tup[1], reverse=True)
sorted_by_second[:100]

In [ ]:
def Wij(token,doc, tf, IDF,doc_to_index):
    return max(tf[token][doc_to_index[doc]]*IDF[token],0.0)

In [ ]:
vocab =set()
for _, split in obj.splitted_word.items():
    vocab.update(split)
    print(vocab)

vocab = list(vocab)
vocab.sort()

In [19]:
vocabulary

[]

In [ ]:
corpus = obj.read_file(doc_path)



In [ ]:
corpus =[]
full=0
with open(doc_path,'r', encoding='utf-8') as file:
    lines = file.readlines()
    print(lines)
    if full==0:
        lines = lines[int(len(lines)/2):]

    for line in lines:
        doc = json.loads(line.strip())
        text = doc['title'] +'. ' + doc['abstract']
        corpus.append(simple_obj.remove_non_ascii(text))
corpus

In [80]:
obj.read_file(doc_path)

[]

In [10]:
range(1,11)

range(1, 11)

In [ ]:
# def SimpleTokenizer(path):
#     corpus =[]
#     with open(path,'r', encoding='utf-8') as file:
#         for line in file:
#             line = json.loads(line.strip())
#             corpus.extend([line['title'], line['abstract']])
            
#     all_tokens=[]
#     for line in corpus:
#         tokens = re.split(PATTERN, line)
#         tokens = [token for token in tokens if token]
#         all_tokens.extend(tokens)

#     tokens = list(set(all_tokens))
#     with open('output.dict','w') as file:
#         file.write('\n'.join(tokens))

In [57]:
['[PAD]'] +['[PAD]', '[UNK]', '[CLS]', '[SEP]', '[MASK]'] 

['[PAD]', '[PAD]', '[UNK]', '[CLS]', '[SEP]', '[MASK]']

In [63]:
def get_corpus(path='test'):
    corpus =[]
    with open(path,'r', encoding='utf-8') as file:
        for line in file:
            line = json.loads(line.strip())

            corpus.extend([line['title'], line['abstract']])
    return corpus

def get_training_corpus(path):
    corpus =[]
    with open(path,'r', encoding='utf-8') as file:
        lines = file.readlines()
        n=len(lines)
        training = lines[int(n/2):]
        for line in training:
            line = json.loads(line.strip())

            corpus.extend([line['title'], line['abstract']])
    return corpus

def get_all_tokens(path='test', full=0):
    if full ==1:
        corpus = get_corpus(path)
    else:
        corpus = get_training_corpus(path)
    all_tokens=[]
    pattern = r'[ ,.:;"’]+'
    for line in corpus:
        tokens = re.split(pattern, line)
        
        # Filter out empty tokens
        tokens = [token for token in tokens if token]
        all_tokens.extend(tokens)

    return all_tokens

def Simple_tokenizer(path='test'):
    tokens = list(set(get_all_tokens(path)))
    with open('output.dict','w') as file:
        file.write('\n'.join(tokens))

def add_end_of_word(tokens):
    for i in range(len(tokens)):
        tokens[i] = tokens[i]+"Ġ"
    return tokens

def calc_freq(tokens):
    token_count = Counter()

    for token in tokens:
        token_count[token]+=1
    
    return token_count

def get_alphabets(tokens):
    alphabets = []

    for word in tokens:
        for letter in word:
            if letter not in alphabets:
                alphabets.append(letter)
    alphabets.sort()
    return alphabets

def split_words(tokens):
    splitted_word = {}
    for word in tokens:
        splitted_word[word] = [ch for ch in word]
    
    return splitted_word

def pair_freq(word_freq, splitted_word):
    pair_count = Counter()

    for word, freq in word_freq.items():
        charaters = splitted_word[word]
        n = len(charaters)
        if n==1:
            continue

        for i in range(n -1):
            pair = (charaters[i], charaters[i+1])
            pair_count[pair] += freq
        
    return pair_count
        
def get_best_pair(pair_freqs):
    max_val = max(pair_freqs.values())
    res = list(filter(lambda x: pair_freqs[x] == max_val, pair_freqs))[0]
    return res, max_val

def merges_split_tokens(best_pair, splitted_word):

    for word,split in splitted_word.items():
        # n=len(split)
        if len(split)==1:
            continue
        
        i=0
        while i< len(split) - 1:
            if split[i] == best_pair[0] and split[i+1] == best_pair[1]:
                split = split[:i] + [best_pair[0]+best_pair[1]] + split[i+2:]
            
            i+=1
        
        splitted_word[word] = split
    
    return splitted_word

def BPE_tokenizer(text, merges):
    pattern = r'[ ,.:;"’]+'
    tokens = re.split(pattern, text)
    splitted_words = [[ch for ch in token]  for token in tokens if token]
    # print(splitted_words)

    for pair, merged in merges.items():
        for i, split in enumerate(splitted_words):
            j=0
            while j < len(split)-1:
                if split[j] == pair[0] and split[j+1] == pair[1]:
                    # print(split[:j], [merged], split[j+2:])
                    # print(split, pair)
                    split = split[:j] + [merged] + split[j+2:]
                j+=1
            splitted_words[i]=split
    
    return sum(splitted_words, [])




In [21]:
a= "$$$$a$$"
a.removeprefix("$$")

'$$a$$'

In [ ]:
def split_words(tokens):
    splitted_word = {}
    for word in tokens:
        splitted_word[word] = ["$$"+ch for ch in word]
        splitted_word[word][0].removeprefix("$$")
    return splitted_word

#score(A,B) = (freq(AB)*len(vocab))/ (freq(A)*freq(B))
def calculate_pair_score(splitted_words, word_freq):
    letter_count = Counter()
    pair_count = Counter()

    for word, freq in word_freq.items():
        charaters = splitted_words[word]
        n=len(charaters)

        if n==1:
            letter_count[charaters[0]]+=freq
            continue

        for i in range(n-1):
            pair = (charaters[i], charaters[i+1])
            pair_count[pair] += freq
            letter_count[charaters[i]] +=freq

        letter_count[charaters[-1]] += freq

    score ={}
    for pair,count in pair_count.items():
        score[pair] = count /(letter_count[pair[0] * letter_count[pair[1]]])
    
    return score

def merges_best_pair(splitted_word, best_pair):

    for word,split in splitted_word.items():
        # n=len(split)
        if len(split)==1:
            continue
        
        i=0
        while i< len(split) - 1:
            if split[i] == best_pair[0] and split[i+1] == best_pair[1]:
                merge = best_pair[0] + best_pair[1].removeprefix("$$")
                split = split[:i] + [merge] + split[i+2:]
            
            i+=1
        
        splitted_word[word] = split
    
    return splitted_word
    

In [ ]:
k = 70
vocab = []
while len(vocab) < k:
    scores = calculate_pair_score(splits)
    best_pair, max_score = "", None
    for pair, score in scores.items():
        if max_score is None or max_score < score:
            best_pair = pair
            max_score = score
    splits = merge_pair(*best_pair, splits)
    new_token = (
        best_pair[0] + best_pair[1][2:]
        if best_pair[1].startswith("##")
        else best_pair[0] + best_pair[1]
    )
    vocab.append(new_token)

In [102]:
# tokens = get_all_tokens('cord19-trec_covid-docs')
tokens = get_all_tokens('test')
tokens = add_end_of_word(tokens)
merges = {}
vocabulary = get_alphabets(tokens)
freq = calc_freq(tokens)
splitted_word = split_words(freq.keys())
pair_frequencies = pair_freq(freq, splitted_word)

best_pair, _ = get_best_pair(pair_frequencies)
merges = {}
merges[best_pair] = best_pair[0]+best_pair[1]
vocabulary.append(merges[best_pair])

In [107]:
merges.items()

dict_items([(('e', 'Ġ'), 'eĠ'), (('s', 'Ġ'), 'sĠ'), (('i', 'n'), 'in'), (('a', 'n'), 'an'), (('a', 't'), 'at'), (('t', 'h'), 'th'), (('o', 'n'), 'on'), (('a', 'l'), 'al'), (('r', 'e'), 're'), (('d', 'Ġ'), 'dĠ'), (('e', 'n'), 'en'), (('t', 'Ġ'), 'tĠ'), (('t', 'i'), 'ti'), (('e', 'r'), 'er'), (('on', 'Ġ'), 'onĠ'), (('y', 'Ġ'), 'yĠ'), (('th', 'eĠ'), 'theĠ'), (('in', 'Ġ'), 'inĠ'), (('o', 'r'), 'or'), (('r', 'o'), 'ro'), (('f', 'Ġ'), 'fĠ'), (('o', 'fĠ'), 'ofĠ'), (('a', 'r'), 'ar'), (('e', 'sĠ'), 'esĠ'), (('s', 'i'), 'si'), (('a', 'Ġ'), 'aĠ'), (('an', 'dĠ'), 'andĠ'), (('al', 'Ġ'), 'alĠ'), (('at', 'i'), 'ati'), (('t', 'o'), 'to'), (('i', 'c'), 'ic'), (('s', 't'), 'st'), (('in', 'g'), 'ing'), (('ing', 'Ġ'), 'ingĠ'), (('a', 's'), 'as'), (('p', 'ro'), 'pro'), (('e', 'm'), 'em'), (('e', 'l'), 'el'), (('to', 'Ġ'), 'toĠ'), (('e', 'c'), 'ec'), (('e', 'dĠ'), 'edĠ'), (('1', 'Ġ'), '1Ġ'), (('t', 'r'), 'tr'), (('re', 's'), 'res'), (('R', 'N'), 'RN'), (('i', 'l'), 'il'), (('v', 'eĠ'), 'veĠ'), (('t', 'sĠ')

In [126]:
BPE_tokenizer("This is not a token.",merges)

['Th', 'is', 'is', 'n', 'o', 't', 'a', 'to', 'k', 'en']

: 

In [104]:
for i in range(100):
    pair_frequencies = pair_freq(freq, splitted_word)
    if len(pair_frequencies) ==0:
        break
    best_pair, count = get_best_pair(pair_frequencies)
    merges[best_pair] = best_pair[0]+best_pair[1]
    vocabulary.append(merges[best_pair])
    print(best_pair, count, len(vocabulary))
    splitted_word = merges_split_tokens(best_pair, splitted_word)
    # print(splitted_word)

('e', 'Ġ') 175 62
('s', 'Ġ') 137 63
('i', 'n') 115 64
('a', 'n') 93 65
('a', 't') 88 66
('t', 'h') 82 67
('o', 'n') 81 68
('a', 'l') 73 69
('r', 'e') 71 70
('d', 'Ġ') 64 71
('e', 'n') 60 72
('t', 'Ġ') 52 73
('t', 'i') 51 74
('e', 'r') 47 75
('on', 'Ġ') 46 76
('y', 'Ġ') 44 77
('th', 'eĠ') 44 78
('in', 'Ġ') 43 79
('o', 'r') 41 80
('r', 'o') 41 81
('f', 'Ġ') 40 82
('o', 'fĠ') 39 83
('a', 'r') 38 84
('e', 'sĠ') 36 85
('s', 'i') 36 86
('a', 'Ġ') 35 87
('an', 'dĠ') 35 88
('al', 'Ġ') 34 89
('at', 'i') 34 90
('t', 'o') 33 91
('i', 'c') 32 92
('s', 't') 28 93
('in', 'g') 27 94
('ing', 'Ġ') 26 95
('a', 's') 26 96
('p', 'ro') 24 97
('e', 'm') 23 98
('e', 'l') 22 99
('to', 'Ġ') 21 100
('e', 'c') 21 101
('e', 'dĠ') 21 102
('1', 'Ġ') 20 103
('t', 'r') 19 104
('re', 's') 19 105
('R', 'N') 19 106
('i', 'l') 18 107
('v', 'eĠ') 18 108
('t', 'sĠ') 18 109
('u', 'l') 18 110
('a', 'm') 18 111
('o', 'u') 17 112
('g', 'en') 17 113
('p', 'l') 17 114
('v', 'i') 16 115
('c', 'l') 16 116
('p', 'o') 16 117
('ti', 

In [90]:
merges

{('e', 'Ġ'): 'eĠ',
 ('s', 'Ġ'): 'sĠ',
 ('i', 'n'): 'in',
 ('a', 'n'): 'an',
 ('a', 't'): 'at',
 ('t', 'h'): 'th',
 ('o', 'n'): 'on',
 ('a', 'l'): 'al',
 ('r', 'e'): 're',
 ('d', 'Ġ'): 'dĠ',
 ('e', 'n'): 'en',
 ('t', 'Ġ'): 'tĠ',
 ('t', 'i'): 'ti',
 ('e', 'r'): 'er',
 ('on', 'Ġ'): 'onĠ',
 ('y', 'Ġ'): 'yĠ',
 ('th', 'eĠ'): 'theĠ',
 ('in', 'Ġ'): 'inĠ',
 ('o', 'r'): 'or',
 ('r', 'o'): 'ro',
 ('f', 'Ġ'): 'fĠ',
 ('o', 'fĠ'): 'ofĠ',
 ('a', 'r'): 'ar',
 ('e', 'sĠ'): 'esĠ',
 ('s', 'i'): 'si',
 ('a', 'Ġ'): 'aĠ',
 ('an', 'dĠ'): 'andĠ',
 ('al', 'Ġ'): 'alĠ',
 ('at', 'i'): 'ati',
 ('t', 'o'): 'to',
 ('i', 'c'): 'ic',
 ('s', 't'): 'st',
 ('in', 'g'): 'ing',
 ('ing', 'Ġ'): 'ingĠ',
 ('a', 's'): 'as',
 ('p', 'ro'): 'pro',
 ('e', 'm'): 'em',
 ('e', 'l'): 'el',
 ('to', 'Ġ'): 'toĠ',
 ('e', 'c'): 'ec',
 ('e', 'dĠ'): 'edĠ',
 ('1', 'Ġ'): '1Ġ',
 ('t', 'r'): 'tr',
 ('re', 's'): 'res',
 ('R', 'N'): 'RN',
 ('i', 'l'): 'il',
 ('v', 'eĠ'): 'veĠ',
 ('t', 'sĠ'): 'tsĠ',
 ('u', 'l'): 'ul',
 ('a', 'm'): 'am',
 ('o', 'u'):

In [125]:
Simple_tokenizer('cord19-trec_covid-docs')

In [87]:
pre_tokenize_result = tokenizer._tokenizer.pre_tokenizer.pre_tokenize_str(text)

In [65]:
tokens = re.split(pattern, corpus[0])
# Remove empty tokens that might appear due to multiple delimiters
tokens = [token for token in tokens if token]

In [68]:
len(set(tokens))

15

In [ ]:
words = corpus

In [70]:
all_tokens=[]
for line in corpus:
    tokens = re.split(pattern, line)
    
    # Filter out empty tokens
    tokens = [token for token in tokens if token]
    all_tokens.extend(list(set(tokens)))

In [28]:
line

{'title': 'Heterogeneous nuclear ribonucleoprotein A1 regulates RNA synthesis of a cytoplasmic virus',
 'doi': '10.1093/emboj/19.17.4701',
 'date': '2000-09-01',
 'abstract': 'Heterogeneous nuclear ribonucleoprotein (hnRNP A1) is involved in pre-mRNA splicing in the nucleus and translational regulation in the cytoplasm. In the present study, we demonstrate that hnRNP A1 also participates in the transcription and replication of a cytoplasmic RNA virus, mouse hepatitis virus (MHV). Overexpression of hnRNP A1 accelerated the kinetics of viral RNA synthesis, whereas the expression in the cytoplasm of a dominant-negative hnRNP A1 mutant that lacks the nuclear transport domain significantly delayed it. The hnRNP A1 mutant caused a global inhibition of viral mRNA transcription and genomic replication, and also a preferential inhibition of the replication of defective-interfering RNAs. Similar to the wild-type hnRNP A1, the hnRNP A1 mutant complexed with an MHV polymerase gene product, the nuc

In [91]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("gpt2")
from collections import defaultdict

word_freqs = defaultdict(int)


c:\Users\SamratYadav\anaconda3\lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [92]:
corpus = get_corpus(path='test')


In [95]:
pre_tokenize_result = tokenizer._tokenizer.pre_tokenizer.pre_tokenize_str(corpus[0])
pre_tokenized_text = [word for word, offset in pre_tokenize_result]
splits = [[l for l in word] for word in pre_tokenized_text]

In [ ]:

for text in corpus:
    words_with_offsets = tokenizer.backend_tokenizer.pre_tokenizer.pre_tokenize_str(text)
    new_words = [word for word, offset in words_with_offsets]
    for word in new_words:
        word_freqs[word] += 1

print(word_freqs)